# Route Visualisations

### Importing all libraries and data needed

In [1]:
import numpy as np
import pandas as pd
import folium
import time
import openrouteservice as ors
import warnings
warnings.simplefilter(action='ignore', category=FutureWarning)
from linearProgram import optimal_Routes
from linearProgramSat import optimal_routes_weekend

C:\Users\jh220\anaconda\lib\site-packages\pulp\pulp.py:1313: UserWarning: Spaces are not permitted in the name. Converted to '_'
  warnings.warn("Spaces are not permitted in the name. Converted to '_'")


Status: Optimal
Status: Optimal


### Reading in coordinates of stores

In [2]:
locations = pd.read_csv("WoolworthsLocations.csv")
cords = locations[['Long' , 'Lat']]
coords = cords.to_numpy().tolist()
cords_locs = locations[['Store','Long','Lat']]

### Setting up optimal routes

In [3]:
#Initialize the variables for the optimal routes
OptR = optimal_Routes
OptRW = optimal_routes_weekend

11

## Route Visualisations for weekdays

### Route Visualisations of Weekday routes with distribution centre

In [5]:
#My ORSKey
ORSKey= '5b3ce3597851110001cf6248f1e943d6f27f45f38a3d16b210d02c68'
client = ors.Client(key=ORSKey)

#Copyright (c) 2010-2019, Vladimir Agafonkin
#Copyright (c) 2010-2011, CloudMade
#Copyright (c) 2013-2020, Thomas Pointhuber
#All rights reserved.


#Setting up colors to help distinguish the different routes
colors = ['#00FFFF','#458B74','#ffb700','#E3CF57','#000000','#0000FF','#00a80b','#FF4040','#8A360F','#FF6103',
         '#7FFF00','#458B00','#8B4513','#3D59AB','#FF7256','#6b6b6b','#DC143C','#008B8B','#bf32cc','#C1FFC1',
         '#EE1289','#808080','#FF69B4','#8470FF','#00FA9A','#8B5A00','#33A1C9','#FF0000','#F4A460','#8E8E38','#eaff00']
dcentre_icon = folium.features.CustomIcon('https://raw.githubusercontent.com/pointhi/leaflet-color-markers/master/img/marker-icon-grey.png', icon_size=(15,20))


m = folium.Map(location = [-36.949,174.808],zoom_start = 10)
#Setup the marker for the distribution centre
folium.Marker(list(reversed(coords[55])), popup = locations.Store[55], icon = dcentre_icon).add_to(m)

#Set up a timer to ensure that the rate limit for directions is not exceeded
timer = 0
#Loop through every optimal route
for i in range(len(OptR)):
    #array to store the coordinates of the stores
    #Initial node/store which is the distribution centre
    a = [(174.808,-36.949)]
    timer = timer + 1
    if (timer == 20):
        #Prevent the code running for a minute
        time.sleep(60)
        timer = 0
    #For every node in the route get the coords and append it to the array
    #Turn the list into a tuple because the client wants it in tuple form. 
    for r in OptR[i]:
        x = cords_locs.index[cords_locs['Store'] == r].tolist()
        c = tuple((coords[x[0]]))
        a.append(c)
        route = client.directions(
            coordinates = a,
            profile = "driving-hgv",
            format = "geojson",
            validate = False
        )
        #Plot the routes
        folium.PolyLine(locations = [list(reversed(coord))
                                    for coord in 
                                        route['features'][0]['geometry']['coordinates']],color = colors[i], opacity = 0.8).add_to(m)



m

### Route Visualisation of Weekday routes with all stores

In [13]:
#Plot the markers for all the stores

for i in range(0, len(coords)):
    if locations.Type[i] == "Countdown":
        Countdown_icon = folium.features.CustomIcon('https://raw.githubusercontent.com/pointhi/leaflet-color-markers/master/img/marker-icon-green.png', icon_size=(15,20))
        ic = Countdown_icon
    elif locations.Type[i] == "FreshChoice":
        FreshChoice_icon = folium.features.CustomIcon('https://raw.githubusercontent.com/pointhi/leaflet-color-markers/master/img/marker-icon-blue.png', icon_size=(15,20))
        ic = FreshChoice_icon
    elif locations.Type[i] == "SuperValue":
        SuperValue_icon = folium.features.CustomIcon('https://raw.githubusercontent.com/pointhi/leaflet-color-markers/master/img/marker-icon-orange.png', icon_size=(15,20))
        ic = SuperValue_icon
    elif locations.Type[i] == "Countdown Metro":
        Countdown_Metro = folium.features.CustomIcon('https://raw.githubusercontent.com/pointhi/leaflet-color-markers/master/img/marker-icon-violet.png', icon_size=(15,20))
        ic = Countdown_Metro
    elif locations.Type[i] == "Distribution Centre":
        dcentre_icon = folium.features.CustomIcon('https://raw.githubusercontent.com/pointhi/leaflet-color-markers/master/img/marker-icon-grey.png', icon_size=(15,20))
        ic = dcentre_icon
    folium.Marker(list(reversed(coords[i])), popup= locations.Store[i], icon = ic).add_to(m)
m

## Route Visualisations for Saturday

### Visualisations with Saturday routes only with the distribution centre

In [5]:
ms = folium.Map(location = [-36.949,174.808],zoom_start = 10)

ORSKey= '5b3ce3597851110001cf6248f1e943d6f27f45f38a3d16b210d02c68'
client = ors.Client(key=ORSKey)

#Copyright (c) 2010-2019, Vladimir Agafonkin
#Copyright (c) 2010-2011, CloudMade
#Copyright (c) 2013-2020, Thomas Pointhuber
#All rights reserved.


Satcolors = ['#00FFFF','#458B74','#ffb700','#E3CF57','#000000','#0000FF','#00a80b','#FF4040','#8A360F','#FF6103',
         '#7FFF00','#458B00']

#Setup the marker for the distribution centre
dcentre_icon = folium.features.CustomIcon('https://raw.githubusercontent.com/pointhi/leaflet-color-markers/master/img/marker-icon-grey.png', icon_size=(15,20))
folium.Marker(list(reversed(coords[55])), popup = locations.Store[55], icon = dcentre_icon).add_to(ms)

#Implement a timer so the rate limit for getting directions is not exceeded
timer = 0
#Loop through every optimal route
for i in range(len(OptRW)):
    #array to store the coordinates of the stores
    #Initial node/store which is the distribution centre
    a = [(174.808,-36.949)]
    timer = timer + 1
    if (timer == 5):
        time.sleep(60)
        timer = 0
    #For every node in the route get the coords and append it to the array
    #Turn the list into a tuple because the client wants it in tuple form. 
    for r in OptRW[i]:
        x = cords_locs.index[cords_locs['Store'] == r].tolist()
        c = tuple((coords[x[0]]))
        a.append(c)
        route = client.directions(
            coordinates = a,
            profile = "driving-hgv",
            format = "geojson",
            validate = False
        )
        #Plot the routes
        folium.PolyLine(locations = [list(reversed(coord))
                                    for coord in 
                                        route['features'][0]['geometry']['coordinates']],color = Satcolors[i], opacity = 0.8).add_to(ms)

ms

### Visualisation of Saturday routes with all stores

In [6]:
#Plot the markers for all the stores

for i in range(0, len(coords)):
    if locations.Type[i] == "Countdown":
        Countdown_icon = folium.features.CustomIcon('https://raw.githubusercontent.com/pointhi/leaflet-color-markers/master/img/marker-icon-green.png', icon_size=(15,20))
        ic = Countdown_icon
    elif locations.Type[i] == "FreshChoice":
        FreshChoice_icon = folium.features.CustomIcon('https://raw.githubusercontent.com/pointhi/leaflet-color-markers/master/img/marker-icon-blue.png', icon_size=(15,20))
        ic = FreshChoice_icon
    elif locations.Type[i] == "SuperValue":
        SuperValue_icon = folium.features.CustomIcon('https://raw.githubusercontent.com/pointhi/leaflet-color-markers/master/img/marker-icon-orange.png', icon_size=(15,20))
        ic = SuperValue_icon
    elif locations.Type[i] == "Countdown Metro":
        Countdown_Metro = folium.features.CustomIcon('https://raw.githubusercontent.com/pointhi/leaflet-color-markers/master/img/marker-icon-violet.png', icon_size=(15,20))
        ic = Countdown_Metro
    elif locations.Type[i] == "Distribution Centre":
        dcentre_icon = folium.features.CustomIcon('https://raw.githubusercontent.com/pointhi/leaflet-color-markers/master/img/marker-icon-grey.png', icon_size=(15,20))
        ic = dcentre_icon
    folium.Marker(list(reversed(coords[i])), popup= locations.Store[i], icon = ic).add_to(ms)
ms